In [37]:
import sys
from datetime import datetime
sys.path.append('../../Scripts')
from preprocess_daily import DailyPreprocessor
self = DailyPreprocessor()

# 1. 데이터 준비
self.load_data()

self.make_match1()
self.make_match2()
self.make_match3()
self.make_match4()
self.make_match5()

1. 데이터를 로드합니다.
1-1. 네트워크가 로드되었습니다.
1-2. 테이블들이 로드되었습니다.
1-3. 네트워크의 모든 clean state requirement들을 체크했습니다.
1-4. 테이블들의 무결성 검사를 완료했습니다.


이동류정보 불러오는 중: 100%|██████████| 17280/17280 [00:13<00:00, 1247.47it/s]


In [36]:
self.node2inter = dict(zip(self.inter_node['node_id'], self.inter_node['inter_no']))

child_ids = self.inter_node[self.inter_node.inter_type=='child'].node_id.unique()
ch2pa = {} # child to parent
for child_id in child_ids:
    parent_no = self.inter_node[self.inter_node.node_id==child_id].inter_no.iloc[0]
    sub_inter_node = self.inter_node[self.inter_node.inter_no==parent_no]
    ch2pa[child_id] = sub_inter_node[sub_inter_node.inter_type=='parent'].iloc[0].node_id
directions = ['북', '북동', '동', '남동', '남', '남서', '서', '북서'] # 정북기준 시계방향으로 8방향

# 각 uturn node에 대하여 (inc_edge_id, out_edge_id) 부여
cmatches = []
for _, row in self.uturn.iterrows():
    child_id = row.child_id
    parent_id = row.parent_id
    direction = row.direction
    condition = row.condition
    inc_edge_id = row.inc_edge
    out_edge_id = row.out_edge
    # match5에서 parent_id에 해당하는 행들을 가져옴
    cmatch = self.match5.copy()[self.match5.node_id==parent_id] # match dataframe for a child node
    cmatch = cmatch.sort_values(by=['phase_no', 'ring_type']).reset_index(drop=True)
    cmatch['node_id'] = child_id
    cmatch[['inc_edge', 'out_edge']] = np.nan

    # condition 별로 inc_dire, out_dire_A, out_dire_B를 정함
    ind = directions.index(direction)
    if condition == "좌회전시":
        inc_dire = direction
        out_dire_A = out_dire_B = directions[(ind + 2) % len(directions)]
    elif condition == "보행신호시":
        inc_dire = directions[(ind + 2) % len(directions)]
        out_dire_A = directions[(ind - 2) % len(directions)]
        out_dire_B = directions[(ind - 2) % len(directions)]
    print(child_id, ((cmatch.inc_dir==inc_dire) & (cmatch.out_dir==out_dire_A)).any())
    # (inc_dire, out_dire_A, out_dire_B) 별로 inc_edge_id, out_edge_id를 정함
    cmatch.loc[(cmatch.inc_dir==inc_dire) & (cmatch.out_dir==out_dire_A), ['inc_edge', 'out_edge']] = [inc_edge_id, out_edge_id]
    cmatch.loc[(cmatch.inc_dir==inc_dire) & (cmatch.out_dir==out_dire_B), ['inc_edge', 'out_edge']] = [inc_edge_id, out_edge_id]
    if condition == '보행신호시':
        # 이동류번호가 17(보행신호)이면서 유턴노드방향으로 가는 신호가 없으면 (inc_edge_id, out_edge_id)를 부여한다.
        cmatch.loc[(cmatch.move_no==17) & (cmatch.out_dir!=direction), ['inc_edge', 'out_edge']] = [inc_edge_id, out_edge_id]
    # 유턴신호의 이동류번호를 19로 부여한다.
    cmatch.loc[(cmatch.inc_dir==inc_dire) & (cmatch.out_dir==out_dire_A), 'move_no'] = 19
    cmatch.loc[(cmatch.inc_dir==inc_dire) & (cmatch.out_dir==out_dire_B), 'move_no'] = 19
    cmatches.append(cmatch)

# 각 coordination node에 대하여 (inc_edge_id, out_edge_id) 부여
self.coord['inter_no'] = self.coord['parent_id'].map(self.node2inter)
self.coord = self.coord.rename(columns={'child_id':'node_id'})
self.coord[['inc_dir', 'out_dir', 'inc_angle','out_angle']] = np.nan
self.coord['move_no'] = 20
self.coord = self.coord[['inter_no', 'phase_no', 'ring_type', 'move_no', 'inc_dir', 'out_dir', 'inc_angle','out_angle', 'inc_edge', 'out_edge', 'node_id']]

# display(coord)
cmatches = pd.concat(cmatches)
self.match6 = pd.concat([self.match5, cmatches, self.coord]).drop_duplicates().sort_values(by=['inter_no', 'node_id', 'phase_no', 'ring_type'])
# self.match6.to_csv(os.path.join(self.path_intermediates, 'match6.csv'))

u00 True
u20 False
u30 True
u31 True
u32 True
u60 True


In [34]:
self.match6

inter_no  phase_no ring_type  move_no inc_dir out_dir inc_angle out_angle  \
0        175         1         A        8       남       북       179       004   
1        175         1         B        4       북       남       003       176   
2        175         2         A        7       북       동       001       095   
3        175         2         B        3       남       서       179       270   
4        175         3         A        6       동       서       090       270   
..       ...       ...       ...      ...     ...     ...       ...       ...   
3        210         2         B        2       서       동       270       090   
4        210         3         A        7       북       동       359       090   
5        210         3         B        4       북       남       000       180   
6        210         4         A        8       남       북       180       000   
7        210         4         B        3       남       서       180       270   

         inc_edge      out_edge node_id  
0   -571542797_02  571500487_01      i0  
1   -571500487_01  571542797_02      i0  
2   -571500487_01  571545870_01      i0  
3   -571542797_02  571510153_01      i0  
4    571545870_02  571510153_01      i0  
..            ...           ...     ...  
3             NaN           NaN     u60  
4             NaN           NaN     u60  
5             NaN           NaN     u60  
6             NaN           NaN     u60  
7             NaN           NaN     u60  

[116 rows x 11 columns]

splits 딕셔너리 다시 만들기

In [53]:
import numpy as np
row = self.plan.iloc[0]
inter_no = row.inter_no
start_hour = row.start_hour
start_minute = row.start_minute
cycle = row.cycle
print(row[[f'dura_A{j}' for j in range(1,9)]])
print(row[[f'dura_B{j}' for j in range(1,9)]])


dura_A = row[[f'dura_A{j}' for j in range(1, 9)]]
dura_B = row[[f'dura_B{j}' for j in range(1, 9)]]

duration_dict = {}
# 두 시리즈의 길이가 같다고 가정합니다.
for i in range(len(dura_A)):
    # A와 B의 현시간이 같은 경우
    if dura_A[i] == dura_B[i]:
        duration_dict[(i+1, i+1)] = dura_A[i]
    # A와 B의 현시간이 다른 경우
    else:
        duration_dict[(i+1, i+1)] = min(dura_A[i], dura_B[i])
        duration_dict[(i+1, i+2)] = max(dura_A[i], dura_B[i])

print(duration_dict)
# cums_A = row[[f'dura_A{j}' for j in range(1,9)]].cumsum()
# cums_B = row[[f'dura_B{j}' for j in range(1,9)]].cumsum()
# print(cums_A)
# print(cums_B)
# detailed_cums = []
# combined_row = np.unique(np.concatenate((cums_A,cums_B)))
# print(combined_row)
# detailed_durations = np.concatenate(([combined_row[0]], np.diff(combined_row)))
# print(detailed_durations)

dura_A1    37
dura_A2    39
dura_A3    55
dura_A4    29
dura_A5     0
dura_A6     0
dura_A7     0
dura_A8     0
Name: 0, dtype: int64
dura_B1    37
dura_B2    39
dura_B3    25
dura_B4    59
dura_B5     0
dura_B6     0
dura_B7     0
dura_B8     0
Name: 0, dtype: int64


NameError: name 'dura_A' is not defined

In [38]:
# split, isplit : A,B 분리 혹은 통합시 사용될 수 있는 딕셔너리 
self.splits = {} # splits maps (inter_no, start_hour, start_minute) to split 
for i, row in self.plan.iterrows():
    inter_no = row.inter_no
    start_hour = row.start_hour
    start_minute = row.start_minute
    cycle = row.cycle
    cums_A = row[[f'dura_A{j}' for j in range(1,9)]].cumsum()
    cums_B = row[[f'dura_B{j}' for j in range(1,9)]].cumsum()
    self.splits[(inter_no, start_hour, start_minute)] = {} # split maps (phas_A, phas_B) to k
    k = 0
    for t in range(cycle):
        new_phas_A = len(cums_A[cums_A < t]) + 1
        new_phas_B = len(cums_B[cums_B < t]) + 1
        if k == 0 or ((new_phas_A, new_phas_B) != (phas_A, phas_B)):
            k += 1
        phas_A = new_phas_A
        phas_B = new_phas_B
        self.splits[(inter_no, start_hour, start_minute)][(phas_A, phas_B)] = k
self.isplits = {} # the inverse of splits
for i in self.splits:
    self.isplits[i] = {self.splits[i][k]:k for k in self.splits[i]} # isplit maps k to (phas_A, phas_B)


In [49]:
self.splits

{(175, 0, 0): {(1, 1): 1, (2, 2): 2, (3, 3): 3, (3, 4): 4, (4, 4): 5},
 (175, 7, 0): {(1, 1): 1, (2, 2): 2, (3, 3): 3, (3, 4): 4, (4, 4): 5},
 (175, 9, 0): {(1, 1): 1, (2, 2): 2, (3, 3): 3, (3, 4): 4, (4, 4): 5},
 (175, 18, 30): {(1, 1): 1, (2, 2): 2, (3, 3): 3, (3, 4): 4, (4, 4): 5},
 (176, 0, 0): {(1, 1): 1, (2, 2): 2, (3, 3): 3},
 (176, 7, 0): {(1, 1): 1, (2, 2): 2, (3, 3): 3},
 (176, 9, 0): {(1, 1): 1, (2, 2): 2, (3, 3): 3},
 (176, 18, 30): {(1, 1): 1, (2, 2): 2, (3, 3): 3},
 (177, 0, 0): {(1, 1): 1, (2, 2): 2, (3, 3): 3, (4, 4): 4},
 (177, 7, 0): {(1, 1): 1, (2, 2): 2, (3, 3): 3, (4, 4): 4},
 (177, 9, 0): {(1, 1): 1, (2, 2): 2, (3, 3): 3, (4, 4): 4},
 (177, 18, 30): {(1, 1): 1, (2, 2): 2, (3, 3): 3, (4, 4): 4},
 (178, 0, 0): {(1, 1): 1, (2, 2): 2, (3, 3): 3, (4, 4): 4},
 (178, 7, 0): {(1, 1): 1, (2, 2): 2, (3, 3): 3, (4, 3): 4, (4, 4): 5},
 (178, 9, 0): {(1, 1): 1, (2, 2): 2, (3, 3): 3, (4, 3): 4, (4, 4): 5},
 (178, 18, 30): {(1, 1): 1, (2, 2): 2, (3, 3): 3, (4, 3): 4, (4, 4): 5},